<a href="https://colab.research.google.com/github/tsimut/Final-Project/blob/master/topic_modelling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import nltk
from nltk import FreqDist
#nltk.download('stopwords') # run this one time

In [0]:
import pandas as pd
pd.set_option("display.max_colwidth", 200)
import numpy as np
import re
import spacy

In [0]:
import gensim
from gensim import corpora

In [13]:
pip install spacy

In [6]:
pip install pyLDAvis

     |████████████████████████████████| 1.6MB 2.9MB/s 
  Stored in directory: /root/.cache/pip/wheels/98/71/24/513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
Successfully built pyLDAvis


In [0]:
# libraries for visualization

import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [0]:
from bs4 import BeautifulSoup
import requests
import time

In [26]:
 pip install "requests[security]"

     |████████████████████████████████| 61kB 2.4MB/s 
     |████████████████████████████████| 2.3MB 8.1MB/s 
     |████████████████████████████████| 102kB 29.9MB/s 


In [0]:
customer_comment=[]
customer_rating=[]

In [0]:
#USE BEAUTIFUL SOUP TO SCRAPE REVIEWS FROM WEBSITE AND APPEND THE DATA TO LISTS
page_count = 0
while page_count <10:
   
    url = "https://www.consumeraffairs.com/travel/uber.html?page=%s" %(page_count)
    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')
    reviews=soup.find(id="reviews-container")
    
    comments=soup.find_all("div", class_="rvw-bd ca-txt-bd-2")
    for ct in comments:
        customer_comment.append(ct.find("p").get_text())

    #try:
    star=reviews.find_all("div",class_="rvw__hdr-stat")
    for st in star:
      customer_rating.append(st.find("img")["data-rating"])
    #except:
        #continue
    page_count += 1
    

In [8]:
Reviews = pd.DataFrame({
"Review":customer_comment,    
"Rating": customer_rating
})


Reviews.head()

Review Rating
0  I have had a few great experiences and a couple of bad experiences. Worst experience was being picked up in an emergency situation when I needed to get to the hospital to visit someone. I was in a...    4.0
1  I’ve never used Lyft before, and the only cab company is highly ineffective. Uber, oddly enough, has attracted highly qualified, a very polite, drivers who drive Uber to earn extra money. I enjoy ...    5.0
2  I've never had a negative experience with Uber. It was the one I downloaded first while in college and the one I've continue to use these past 3 or so years. Some experiences have been better than...    5.0
3  I have always been skeptical about rideshare services because of the news reports of assaults and robberies. I used this company for the first time earlier this year during a trip for a conference...    4.0
4  I have used Uber several times and so far I am very happy with the company and how easy it's to set up an account. I love that they are constantly upgrading features with their company making cust...    5.0

In [0]:
# remove unwanted characters, numbers and symbols
Reviews['Review'] = Reviews['Review'].str.replace("[^a-zA-Z#]", " ")

In [10]:
#IDENTIFY TOP 10 OCCURING WORDS
freq = pd.Series(' '.join(Reviews['Review']).split()).value_counts()[:10]
freq

I       1045
the      954
to       884
and      838
a        651
Uber     517
my       356
of       330
was      330
is       302
dtype: int64

In [12]:
#REMOVE UNNESSARY WORDS
common_word=("uber",'Uber')
Reviews['Review'] = Reviews['Review'].apply(lambda x: " ".join(x for x in x.split() if x not in common_word))
Reviews['Review'].head()


0    I have had a few great experiences and a couple of bad experiences Worst experience was being picked up in an emergency situation when I needed to get to the hospital to visit someone I was in a h...
1    I ve never used Lyft before and the only cab company is highly ineffective oddly enough has attracted highly qualified a very polite drivers who drive to earn extra money I enjoy that scheduling a...
2    I ve never had a negative experience with It was the one I downloaded first while in college and the one I ve continue to use these past or so years Some experiences have been better than others b...
3    I have always been skeptical about rideshare services because of the news reports of assaults and robberies I used this company for the first time earlier this year during a trip for a conference ...
4    I have used several times and so far I am very happy with the company and how easy it s to set up an account I love that they are constantly upgrading features with their comp

In [0]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

In [14]:
stop = stopwords.words('english')
Reviews['Review'] = Reviews['Review'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))
Reviews['Review'].head()

0    I great experiences couple bad experiences Worst experience picked emergency situation I needed get hospital visit someone I hurry already highway I realized driver reeked alcohol completely intox...
1    I never used Lyft cab company highly ineffective oddly enough attracted highly qualified polite drivers drive earn extra money I enjoy scheduling ride simple smartphone application Once detects lo...
2    I never negative experience It one I downloaded first college one I continue use past years Some experiences better others opinion drivers probably worse experience The rides I enjoyed ones driver...
3    I always skeptical rideshare services news reports assaults robberies I used company first time earlier year trip conference Las Vegas My first ride excellent completed without problem My second r...
4    I used several times far I happy company easy set account I love constantly upgrading features company making customer feel safe taking They arrive timely manner drivers I pro

In [15]:
# remove short words (length < 3)
Reviews["Review"] = Reviews["Review"].apply(lambda x: ' '.join([w for w in x.split() if len(w)>2]))
Reviews['Review'] = Reviews['Review'].apply(lambda x: " ".join(x.lower() for x in x.split()))
Reviews['Review'].head()

0    great experiences couple bad experiences worst experience picked emergency situation needed get hospital visit someone hurry already highway realized driver reeked alcohol completely intoxicated w...
1    never used lyft cab company highly ineffective oddly enough attracted highly qualified polite drivers drive earn extra money enjoy scheduling ride simple smartphone application once detects local ...
2    never negative experience one downloaded first college one continue use past years some experiences better others opinion drivers probably worse experience the rides enjoyed ones driver respected ...
3    always skeptical rideshare services news reports assaults robberies used company first time earlier year trip conference las vegas first ride excellent completed without problem second ride little...
4    used several times far happy company easy set account love constantly upgrading features company making customer feel safe taking they arrive timely manner drivers professiona

In [16]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [0]:

from nltk.tokenize import word_tokenize
Reviews['Review'] = Reviews['Review'].apply(word_tokenize) 


In [30]:
nlp = spacy.load('en', disable=['parser'])

def lemmatization(texts,tags=['NOUN', 'ADJ']):
    output = []
    for i in texts:
        s = [token.lemma_ for token in nlp(i)]
        output.append(' '.join(s))
    return output
Reviews['Review'] =lemmatization(Reviews['Review'],tags=['NOUN', 'ADJ'])
Reviews.head(10)

TypeError: ignored

In [19]:
Reviews.head(10)

Review Rating
0  [great, experience, couple, bad, experience, bad, experience, pick, emergency, situation, need, get, hospital, visit, someone, hurry, already, highway, realize, driver, reek, alcohol, completely, ...    4.0
1  [never, use, lyft, cab, company, highly, ineffective, oddly, enough, attract, highly, qualified, polite, driver, drive, earn, extra, money, enjoy, schedule, ride, simple, smartphone, application, ...    5.0
2  [never, negative, experience, one, download, first, college, one, continue, use, past, year, some, experience, well, other, opinion, driver, probably, bad, experience, the, ride, enjoy, one, drive...    5.0
3  [always, skeptical, rideshare, service, news, report, assault, robbery, use, company, first, time, early, year, trip, conference, las, vegas, first, ride, excellent, complete, without, problem, se...    4.0
4  [use, several, time, far, happy, company, easy, set, account, love, constantly, upgrade, feature, company, make, customer, feel, safe, take, -PRON-, arrive, timely, manner, driver, professional, l...    5.0
5  [lip, service, term, driver, quality, india, large, number, car, dirty, acs, hardly, fictional, driver, try, defraud, overcharge, uber, customer, support, india, dismal, driver, overcharge, rupee,...    1.0
6  [request, ride, fort, worth, south, henderson, street, irve, texas, the, upfront, fare, show, economy, ride, say, offer, max, per, ride, discount, driver, aashish, toyota, corolla, come, literally...    1.0
7  [earlier, great, -PRON-, use, provide, prompt, customer, service, quick, redressal, issue, now, person, speak, acknowledgement, even, complain, random, multiple, charge, deduct, trip, thank, god, ...    1.0
8  [use, rider, good, passenger, rating, never, issue, driver, experience, general, good, month, ago, disabled, account, reach, customer, support, email, exchange, customer, support, send, rude, offe...    1.0
9  [eat, cancel, order, without, refund, ubereat, friend, don, order, food, eat, get, money, deliver, food, that, experience, story, -PRON-, customer, support, resolve, problem, the, delivery, boy, c...    1.0

In [23]:
reviews_list = [item for items in Reviews['Review'] for item in items]

reviews_list

['great',
 'experience',
 'couple',
 'bad',
 'experience',
 'bad',
 'experience',
 'pick',
 'emergency',
 'situation',
 'need',
 'get',
 'hospital',
 'visit',
 'someone',
 'hurry',
 'already',
 'highway',
 'realize',
 'driver',
 'reek',
 'alcohol',
 'completely',
 'intoxicate',
 'weaving',
 'lane',
 'could',
 'keep',
 'car',
 'lane',
 'the',
 'second',
 'time',
 'bad',
 'driver',
 'make',
 'couple',
 'stop',
 'along',
 'way',
 'take',
 'destination',
 'these',
 'stop',
 'shady',
 'part',
 'town',
 'scare',
 'death',
 'never',
 'use',
 'lyft',
 'cab',
 'company',
 'highly',
 'ineffective',
 'oddly',
 'enough',
 'attract',
 'highly',
 'qualified',
 'polite',
 'driver',
 'drive',
 'earn',
 'extra',
 'money',
 'enjoy',
 'schedule',
 'ride',
 'simple',
 'smartphone',
 'application',
 'once',
 'detect',
 'local',
 'driver',
 'via',
 'gps',
 'direct',
 'close',
 'driver',
 'available',
 'provide',
 'estimate',
 'time',
 'wait',
 'estimate',
 'time',
 'arrival',
 'destination',
 'also',
 'allo

In [0]:

dictionary = corpora.Dictionary(Reviews['Review'])

In [0]:
doc_term_matrix = [dictionary.doc2bow(rev) for rev in Reviews['Review']]

In [27]:
# Creating the object for LDA model using gensim library
LDA = gensim.models.ldamodel.LdaModel
# Build LDA model
lda_model = LDA(corpus=doc_term_matrix, id2word=dictionary, num_topics=7, random_state=100,
                chunksize=1000, passes=50)

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for

In [28]:
lda_model.print_topics()

[(0,
  '0.022*"use" + 0.019*"driver" + 0.015*"ride" + 0.012*"card" + 0.012*"phone" + 0.012*"email" + 0.011*"app" + 0.010*"get" + 0.010*"charge" + 0.009*"go"'),
 (1,
  '0.026*"ride" + 0.020*"say" + 0.013*"get" + 0.013*"car" + 0.012*"go" + 0.012*"take" + 0.010*"driver" + 0.010*"charge" + 0.009*"end" + 0.009*"book"'),
 (2,
  '0.037*"driver" + 0.015*"use" + 0.010*"trip" + 0.010*"take" + 0.009*"great" + 0.009*"get" + 0.009*"the" + 0.008*"ask" + 0.008*"company" + 0.008*"app"'),
 (3,
  '0.022*"driver" + 0.014*"get" + 0.014*"time" + 0.014*"take" + 0.013*"charge" + 0.013*"car" + 0.012*"ride" + 0.010*"customer" + 0.009*"pay" + 0.009*"money"'),
 (4,
  '0.013*"get" + 0.013*"customer" + 0.012*"order" + 0.011*"-PRON-" + 0.011*"call" + 0.011*"try" + 0.011*"the" + 0.010*"service" + 0.010*"time" + 0.010*"use"'),
 (5,
  '0.039*"driver" + 0.022*"time" + 0.016*"use" + 0.013*"ride" + 0.012*"drive" + 0.010*"get" + 0.009*"the" + 0.008*"-PRON-" + 0.008*"cab" + 0.007*"take"'),
 (6,
  '0.019*"driver" + 0.013*"u

In [29]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, doc_term_matrix, dictionary)
vis

/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3      0.026082 -0.015497       1        1  25.847986
4      0.087361 -0.035692       2        1  21.414915
5     -0.027467  0.097539       3        1  15.850144
0      0.099493 -0.049176       4        1  15.520895
2     -0.028814  0.096849       5        1   9.169393
6     -0.019958  0.008841       6        1   7.424070
1     -0.136697 -0.102863       7        1   4.772601, topic_info=    Category        Freq        Term       Total  loglift  logprob
10   Default  272.000000      driver  272.000000  30.0000  30.0000
77   Default  149.000000        ride  149.000000  29.0000  29.0000
242  Default   66.000000         say   66.000000  28.0000  28.0000
154  Default   45.000000       phone   45.000000  27.0000  27.0000
4    Default   88.000000         car   88.000000  26.0000  26.0000
84   Default  153.000000         use  153.000000  25.0000  25.0000
466  Default   44.000000        card   44.000000  24.0000  24.0000
149  Default   69.000000          go   69.000000  23.0000  23.0000
321  Default   48.000000       order   48.000000  22.0000  22.0000
320  Default   25.000000        food   25.000000  21.0000  21.0000
33   Default   99.000000        take   99.000000  20.0000  20.0000
167  Default   67.000000         try   67.000000  19.0000  19.0000
55   Default   61.000000       drive   61.000000  18.0000  18.0000
285  Default   48.000000       email   48.000000  17.0000  17.0000
243  Default   42.000000        show   42.000000  16.0000  16.0000
14   Default   29.000000       great   29.000000  15.0000  15.0000
226  Default   17.000000         end   17.000000  14.0000  14.0000
220  Default  102.000000      charge  102.000000  13.0000  13.0000
315  Default   35.000000      cancel   35.000000  12.0000  12.0000
378  Default   32.000000         new   32.000000  11.0000  11.0000
50   Default   64.000000     company   64.000000  10.0000  10.0000
527  Default   32.000000     contact   32.000000   9.0000   9.0000
87   Default   40.000000        wait   40.000000   8.0000   8.0000
232  Default   24.000000        home   24.000000   7.0000   7.0000
393  Default   19.000000        book   19.000000   6.0000   6.0000
228  Default   22.000000        fare   22.000000   5.0000   5.0000
140  Default   30.000000        come   30.000000   4.0000   4.0000
452  Default   12.000000     license   12.000000   3.0000   3.0000
300  Default   25.000000   passenger   25.000000   2.0000   2.0000
537  Default   12.000000        gift   12.000000   1.0000   1.0000
..       ...         ...         ...         ...      ...      ...
226   Topic7    5.470765         end   17.637747   1.8717  -4.6825
393   Topic7    5.154145        book   19.446404   1.7144  -4.7421
242   Topic7   11.688639         say   66.159439   1.3088  -3.9233
913   Topic7    2.333664    daughter    6.291924   2.0505  -5.5344
219   Topic7    2.838401        busy    8.670895   1.9255  -5.3386
77    Topic7   15.315831        ride  149.291275   0.7653  -3.6530
228   Topic7    4.515456        fare   22.455801   1.4382  -4.8744
239   Topic7    2.838217         per   10.355610   1.7479  -5.3387
238   Topic7    2.027020         non    5.581319   2.0294  -5.6753
149   Topic7    7.150540          go   69.203682   0.7724  -4.4147
232   Topic7    4.197258        home   24.525665   1.2770  -4.9475
4     Topic7    7.485173         car   88.423393   0.5731  -4.3690
154   Topic7    5.064895       phone   45.864937   0.8389  -4.7595
33    Topic7    6.908268        take   99.987808   0.3699  -4.4492
13    Topic7    7.949463         get  146.347549   0.1294  -4.3088
243   Topic7    4.442523        show   42.152538   0.7922  -4.8907
405   Topic7    2.832717         min   12.571987   1.5520  -5.3406
167   Topic7    5.109320         try   67.208885   0.4655  -4.7508
123   Topic7    3.395911        taxi   22.367960   1.1572  -5.1593
87    Topic7    4.217830        wait   40.882034   0.7

In [0]:
# function to plot most frequent terms
def freq_words(x, terms = 30):
  all_words = ' '.join([text for text in x])
  all_words = all_words.split()